# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model
(Recurrent PPO) [default: 25 EVs per week simulation]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
from google.colab import drive
drive.mount('/content/drive')

%cd /content/drive/MyDrive/DAI-Labor/RL_VPP_Thesis/
%ls

Mounted at /content/drive
/content/drive/MyDrive/DAI-Labor/RL_VPP_Thesis
Agent_trainer_notebooks/          __pycache__/
Algorithm_simulator_notebooks/    README.md
data/                             trained_models/
EV_experiment_notebooks/          VPP_environment.py
Hyperparameters_sweep_notebooks/  VPP_simulator.ipynb
log.log                           wandb/


In [3]:
# #Cloning repository and changing directory
# !git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
# %cd RL_VPP_Thesis/
# %ls

In [4]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [5]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [6]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7ff8485d6950>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 25
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 25, 'EVs_n_max': 1305, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [7]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_Dataset_autarky()

Charging event: 1, Arrival time: 2022-01-01 18:15:00, Parking_time: 24, Leaving_time: 2022-01-02 18:15:00, SOC: 0.5325630474880791, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1304, Arrival time: 2022-12-31 16:15:00, Parking_time: 23.416881112724376, Leaving_time: 2023-01-01 15:40:00.772006, SOC: 0.38719155471548633, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en(grid-import)=4947.18kWh , autarky-rate=83.0 , RE-to-vehicle_unused_en(grid-export)=-26161.81kWh , self-consump.rate=47.9 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  28665.76 , Grid_used_en=kWh  44292.62 , RE-to-vehicle_unused_en=kWh  15626.86 , Total_selling_cost=€  1115.8 , Grid_cost=€  1562.22 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06


In [8]:
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [9]:
env.plot_ELVIS_data()

In [10]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27322.42 , Grid_used_en(grid-import)=43980.01kWh , Total_demand=77586.55kWh , autarky-rate=0.4 , RE-to-vehicle_unused_en(grid-export)=16657.59kWh , Total_supply=50264.13kWh , self-consump.rate=0.7 , Grid_cost=€  1560.71 , Total_selling_cost=€  1075.8 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [11]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
#env.plot_Elvis_results()

In [13]:
#env.plot_VPP_results()

In [14]:
env.plot_VPP_autarky()

In [15]:
env.plot_VPP_supply_demand()

In [16]:
env.plot_VPP_Elvis_comparison()

In [17]:
env.plot_rewards_results()

In [18]:
#env.plot_rewards_stats()

In [19]:
env.plot_EVs_kpi()

In [20]:
env.plot_actions_kpi()

In [21]:
env.plot_load_kpi()

In [22]:
env.plot_yearly_load_log()

In [23]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [24]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [25]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27472.67 , Grid_used_en(grid-import)=44203.19kWh , Total_demand=77729.27kWh , autarky-rate=0.4 , RE-to-vehicle_unused_en(grid-export)=16730.52kWh , Total_supply=50256.6kWh , self-consump.rate=0.7 , Grid_cost=€  1556.84 , Total_selling_cost=€  1087.08 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2770.25 , Grid_used_en(grid-import)=1760.25kWh , Total_demand=61917.37kWh , autarky-rate=97.2 , RE-to-vehicle_unused_en(grid-export)=4530.5kWh , Total_supply=64687.62kWh , self-consump.rate=93.0 , Total_selling_cost=€  -45.8 , Grid_cost=€  61.63 
 EV_INFO: Av.EV_energy_leaving=kWh  64.1 , Std.EV_energy_leaving=kWh  23.6 , EV_departures =  1303 , EV_queue_left =  0
SCORE:  Cumulative_reward= 443777.52 - Step_rewars (load_t= 404461.04, EVs_energy_

In [26]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  48.935398   0.000000  37.090614   0.000000   
2022-01-01 00:15:00  47.870178   0.000000  37.340614   0.000000   
2022-01-01 00:30:00  46.995987   0.000000  37.590614   0.000000   
2022-01-01 00:45:00  46.482540   0.000000  37.840614   0.000000   
2022-01-01 01:00:00  45.794403   0.000000  38.090614   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  48.264561  43.011944  37.082977  79.888237   
2022-06-06 05:00:00  49.353737  42.761944  38.172153  80.977409   
2022-06-06 05:15:00  50.448963  42.511944  39.267380  82.072639   
2022-06-06 05:30:00  51.551472  42.261944  40.369888  83.175148   
2022-06-06 05:45:00  52.245083  42.955555  41.063499  83.868759   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 0, 1, 2]   
2022-01-01 00:15:00        [3911, 0, 3912, 0]  [2, 0, 1, 2]   
2022-01-01 00:30:00        [3911, 0, 3912, 0]  [2, 0, 1, 2]   
2022-01-01 00:45:00        [3911, 0, 3912, 0]  [2, 0, 1, 2]   
2022-01-01 01:00:00        [3911, 0, 3912, 0]  [2, 0, 1, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [4462, 4461, 4460, 4459]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [4462, 4461, 4460, 4459]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [4462, 4461, 4460, 4459]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [4462, 4461, 4460, 4459]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [4462, 4461, 4460, 4459]  [1, 1, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, True, False, False]        0.000000   
2022-01-01 00:15:00   [True, True, False, False]        1.000000   
2022-01-01 00:30:00   [True, True, False, False]        1.000000   
2022-01-01 00:45:00   [True, True, False, False]        1.000000   
2022-01-01 01:00:00   [True, True, False, False]        1.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, False, True, True]       11.589818   
2022-06-06 05:00:00    [True, False, True, True]       13.070107   
2022-06-06 05:15:00    [True, False, True, True]       13.142721   
2022-06-06 05:30:00     [True, True, True, True]       13.230085   
2022-06-06 05:45:00     [True, True, True, True]       11.097803   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.337755e+00         15.0        0.0   
2022-01-01 00:15:00          -4.260882  0.000000e+00         15.0        0.0   
2022-01-01 00:30:00          -3.496767  0.000000e+00         15.0        0.0   
2022-01-01 00:45:00          -2.053791  0.000000e+00         15.0        0.0   
2022-01-01 01:00:00          -2.752542  0.000000e+00         15.0        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -2.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:00:00          -1.000000 -1.776357e-15         15.0        0.0   
2022-06-06 05:15:00          -1.000000  1.776357e-15         15.0        0.0   
2022-06-06 05:30:00          -1.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:45:00           0.000000  0.000000e+00         15.0        0.0   

                     rewards  
time                          
2022-01-01 00:00:00     15.0  
2022-01-01 00:15:00     15.0  
2022-01-01 00:30:00     15.0  
2022-01-01 00:45:00     15.0  
2022-01-01 01:00:00     15.0  
...                      ...  
2022-06-06 04:45:00     15.0  
2022-06-06 05:00:00     15.0  
2022-06-06 05:15:00     15.0  
2022-06-06 05:30:00     15.0  
2022-06-06 05:45:00     15.0  

[15000 

In [28]:
#env.plot_Elvis_results()

In [29]:
#env.plot_VPP_results()

In [30]:
env.plot_VPP_autarky()

In [31]:
env.plot_VPP_supply_demand()

In [32]:
env.plot_VPP_Elvis_comparison()

In [33]:
env.plot_rewards_results()

In [34]:
env.plot_rewards_stats()

In [35]:
env.plot_EVs_kpi()

In [36]:
env.plot_load_kpi()

In [37]:
env.plot_yearly_load_log()

## Validating dataset VPP Simulation using the loaded trained model

In [38]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5217, Arrival time: 2022-01-01 08:45:00, Parking_time: 24, Leaving_time: 2022-01-02 08:45:00, SOC: 0.3083818764770311, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6520, Arrival time: 2022-12-31 09:00:00, Parking_time: 23.988847080230013, Leaving_time: 2023-01-01 08:59:19.849489, SOC: 0.6161637394105004, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en(grid-import)=2136.67kWh , autarky-rate=89.6 , RE-to-vehicle_unused_en(grid-export)=-32222.06kWh , self-consump.rate=36.4 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  17251.44 , Grid_used_en=kWh  38104.27 , RE-to-vehicle_unused_en=kWh  20852.83 , Total_selling_cost=€  842.92 , Grid_cost=€  1694.49 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  74.71


In [39]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [40]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [41]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18671.34 , Grid_used_en(grid-import)=39410.2kWh , Total_demand=69277.76kWh , autarky-rate=0.4 , RE-to-vehicle_unused_en(grid-export)=20738.87kWh , Total_supply=50606.42kWh , self-consump.rate=0.6 , Grid_cost=€  1712.29 , Total_selling_cost=€  865.23 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  74.71
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4357.68 , Grid_used_en(grid-import)=913.68kWh , Total_demand=57813.18kWh , autarky-rate=98.4 , RE-to-vehicle_unused_en(grid-export)=5271.36kWh , Total_supply=62170.86kWh , self-consump.rate=91.5 , Total_selling_cost=€  -158.08 , Grid_cost=€  41.48 
 EV_INFO: Av.EV_energy_leaving=kWh  69.73 , Std.EV_energy_leaving=kWh  23.61 , EV_departures =  1301 , EV_queue_left =  0
SCORE:  Cumulative_reward= 476318.6 - Step_rewars (load_t= 406992.61, EVs_energ

In [42]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [43]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000  58.319885   0.000000   0.000000   
2022-01-01 01:00:00   0.000000  59.267639   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  61.244587  57.003410  72.389320  73.913513   
2022-06-06 05:00:00  62.504261  56.753410  73.648994  75.173187   
2022-06-06 05:15:00  63.347927  57.597076  74.492661  76.016853   
2022-06-06 05:30:00  64.186203  58.435352  75.330933  76.855125   
2022-06-06 05:45:00  65.104126  59.353275  76.248856  77.773048   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00           [0, 7825, 0, 0]  [0, 1, 0, 2]   
2022-01-01 01:00:00           [0, 7825, 0, 0]  [0, 1, 2, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [8375, 8372, 8373, 8374]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [8375, 8372, 8373, 8374]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [8375, 8372, 8373, 8374]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [8375, 8372, 8373, 8374]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [8375, 8372, 8373, 8374]  [1, 1, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00    [True, True, True, False]        0.000000   
2022-01-01 01:00:00   [True, True, False, False]        3.791017   
...                                          ...             ...   
2022-06-06 04:45:00    [True, False, True, True]        7.518505   
2022-06-06 05:00:00     [True, True, True, True]       15.116092   
2022-06-06 05:15:00     [True, True, True, True]       13.498680   
2022-06-06 05:30:00     [True, True, True, True]       13.412394   
2022-06-06 05:45:00     [True, True, True, True]       14.686747   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -4.185602    -5.380381        0.0   
2022-01-01 00:15:00                0.0 -4.418419    -3.790824        0.0   
2022-01-01 00:30:00                0.0 -3.274494    -5.112977        0.0   
2022-01-01 00:45:00                0.0 -4.124274    15.000000        0.0   
2022-01-01 01:00:00                0.0  0.000000    15.000000        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00               -1.0 -3.759240    15.000000        0.0   
2022-06-06 05:00:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00                0.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.380381  
2022-01-01 00:15:00  -3.790824  
2022-01-01 00:30:00  -5.112977  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:45:00  15.000000  

[15000 rows x 13 columns]

In [44]:
#env.plot_VPP_results()


In [45]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_supply_demand()

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 9129, Arrival time: 2022-01-01 13:15:00, Parking_time: 22.366206881280082, Leaving_time: 2022-01-02 11:36:58.344773, SOC: 0.34192628590543356, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 10432, Arrival time: 2022-12-31 17:15:00, Parking_time: 23.640184209127124, Leaving_time: 2023-01-01 16:53:24.663153, SOC: 0.4362576452149644, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en(grid-import)=1556.25kWh , autarky-rate=90.5 , RE-to-vehicle_unused_en(grid-export)=-35673.95kWh , self-consump.rate=29.4 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  15060.12 , Grid_used_en=kWh  37149.82 , RE-to-vehicle_unused_en=kWh  22089.7 , Total_selling_cost=€  718.4 , Grid_cost=€  1530.97 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  77.36


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

In [ ]:
env.plot_VPP_energies()

In [ ]:
VPP_table.head(14995)

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_supply_demand()

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

In [ ]:
#env.close()